# Simulation et estimation d'un processus de Hawkes linéaire univarié

In [6]:
import numpy as np
from scipy.stats import kstest
from scipy.optimize import minimize
import pandas as pd
import matplotlib.pyplot as plt
from datetime import datetime

Dans ce TP, on s'intéresse à un processus de Hawkes linéaire exponentiel univarié, dont les temps de saut sont notés $(T_k)_{k\geq 1}$, d'intensité 

$$\lambda(t)=\mu + \sum_{T_k \leq t} \alpha \beta \exp(-\beta(t-T_k)),$$

pour tout $t\in [0,T]$. 

On suppose que les paramètres vérifient les conditions suivantes : $\mu >0$, $0<\alpha <1$ et $\beta>0$.

## Simulation d'un processus de Hawkes par thinning

Ecrire une fonction qui prend en entrée $\mu$, $\alpha$, $\beta$, $T$ et qui renvoie les temps de saut d'une réalisation du processus sur $[0,T]$.

In [1]:
mu=1
alpha=0.5
beta=2
T=100



Remarque : Pour calculer l'intensité au temps candidat, on peut toujours utiliser la formule générale de l'intensité. Dans le cas exponentiel, l'intensité est markovienne, i.e. elle dépend uniquement de l'intensité au dernier temps de saut et du temps écoulé depuis ce dernier saut. On peut alors calculer l'intensité de façon récursive, ce qui est beaucoup moins coûteux en temps de calcul. Pour cela il faut exprimer l'intensité au temps candidat $t^\star$ en fonction de l'intensité au dernier temps $t$.

Tracer l'intensité simulée.

## Comment vérifier la simulation ? 

On va utiliser une procédure d'ajustement qui est un corollaire du théorème de changement de temps (Daley et Vere-Jones, 2003). Ce théorème nous dit que pour un processus ponctuel $(T_k)_{k\geq 1}$ d'intensité $\lambda_\theta(t)$ et de compensateur $\Lambda_\theta(t)=\int_0^t \lambda_\theta(u) du$, le processus $(\Lambda_\theta(T_k))_{k\geq 1}$ est un processus de Poisson d'intensité 1. Autrement dit, les incréments du compensateur $(\Lambda_\theta(T_k))-\Lambda_\theta(T_{k-1})) \sim Exp (1)$. Cette propriété permet donc de formuler la procédure de test suivante pour le processus $(T_k)_{k\geq 1}$ simulé :

- Calculer le compensateur aux temps de sauts : $(\Lambda_\theta(T_k))_{k\geq 1}$

- Calculer les incréments $(\Lambda_\theta(T_k))-\Lambda_\theta(T_{k-1}))$

- Tester si ces incréments sont des exponentielles de paramètre 1, grâce à un test de Kolmogorov-Smirnov.


Ecrire une fonction qui prend en entrée les $T_k$, les paramètres $\mu$, $\alpha$ et $\beta$ et le temps t auquel on calcule le compensateur :

Calculer les incréments du compensateur avec la fonction **np.diff** puis utiliser la fonction **kstest** pour effectuer la procédure de test ci-dessus.

## Estimation

### Fonction de vraisemblance

La log-vraisemblance d'un processus ponctuel d'intensité $\lambda_\theta(t)$ sur $[0, T]$ s'écrit :

$$ \ell_\theta(T) = \sum_{k=1}^{N(T)}log(\lambda_\theta(T_k^{-})) - \Lambda_\theta(T)$$

où $\lambda_\theta(T_k^{-})$ est l'intensité avant le temps de saut $T_k$.

Ecrire une fonction qui prend entrée les $T_k$, $\mu$, $\alpha$, $\beta$, $T$ et qui renvoie la vraisemblance (ou l'opposé de la vraisemblance, qu'on cherchera à minimiser à la question suivante).

### Maximum de vraisemblance

Calculer l'estimateur du maximum de vraisemblance à l'aide de la fonction **minimize**.

- Vous utiliserez la méthode d'optimisation "L-BFGS-B", qui permet notamment de minimiser sous contrainte.
-  Vous pourrez imposer les contraintes sur les paramètres qui doivent rester positifs et $\alpha < 1$ (condition de stabilité du processus).
- Pour l'initialisation, commencer par une initialisation proche des vrais paramètres puis si ça fonctionne, vous pourrez prendre une initialisation aléatoire.


## Données Twitter

On va mettre en pratique votre procédure d'estimation et le test d'ajustement sur des données de Tweets du jeu de données Memetracker. Les données sont à récupérer sur la page suivante : https://snap.stanford.edu/memetracker/data.html

Le code ci-dessous (emprunté à Miguel Martinez Herrera) vous permet de sélectionner un morceau de phrase et de récupérer une liste **timesList** avec les temps auxquels cette séquence de mots a été tweetée. La séquence choisie ici est "workers of the world unite" (vous pouvez changer en modifiant l'indice "indexToExtract").

Estimer les paramètres de ce processus, tracer l'intensité estimée et vérifier l'ajustement d'un processus de Hawkes à ces données.


In [ ]:

if __name__ == "__main__":

    table = pd.read_csv("clust-qt08080902w3mfq5.txt", skiprows=4, sep="	",
                        names=['a', 'b', 'c', 'd', 'e', 'f'])
    index = table.index
    condition = table["a"].notnull()
    index = index[condition]

    print("s")


   ### indice de la séquence de mots
    indexToExtract = 137082
    

    indexInTable = 0
    flag = int(table.iloc[index[indexInTable]]["d"]) == indexToExtract

    while not (flag):
        indexInTable += 1
        flag = int(table.iloc[index[indexInTable]]["d"]) == indexToExtract

    #indexInTable = 8500
    extractedMeme = table.iloc[index[indexInTable]: index[indexInTable + 1]]

    ### Print phrases

    print(extractedMeme.shape)
    for i in range(extractedMeme.shape[0]):
        try:
            int(extractedMeme.iloc[i]["d"])
            pass
        except:
            print(extractedMeme.iloc[i]["d"])

    ### Convert to times

    timesList = []

    for i in range(extractedMeme.shape[0]):
        try:
            timesList += [datetime.strptime(extractedMeme.iloc[i]["c"], "%Y-%m-%d %H:%M:%S").timestamp()]
        except:
            pass

    # timesList = np.unique(np.sort(np.array(timesList) - timesList[0])/100000)
    timesList = np.sort(np.array(timesList) - timesList[0])/100000
